# Galaxy surface brightness analysis

## Selecting your source

In [ ]:
context.set_project('TUTORIAL')
context.set_privileges(1)
print(context.get_current_project())

Identify a source in a SourceList which we want to analyse. Actually you will probably be thinking of an image rather than a SourceList. So lets start with that. Retrieve the image with the following filename: ``Sci-EHELMICH-WFI-------#842---Coadd---Sci-54552.5317447-4d2189f46deed79e536cdbfb0af72ae24187ffd8.fits``.

In [ ]:
c = (CoaddedRegriddedFrame.filename == 'Sci-EHELMICH-WFI-------#842---Coadd---Sci-54552.5317447-4d2189f46deed79e536cdbfb0af72ae24187ffd8.fits')[0]

Lets have a look at this image, and select a galaxy from it.

In [ ]:
c.retrieve()
c.display()

A SourceList exists for this image:

In [ ]:
sl = (SourceList.SLID == 423431)[0]

Make a skycat catalog for the image and find the SID of an interesting source.

In [ ]:
sl.make_skycat_on_sources()

Now overplot the catalog in skycat. Open the file and select *Data-Servers -> Local Catalogs -> Load from file*.... As filter fill in \*.scat. You may need to increase the number of sources to get all of them to display. If you click on a symbol the corresponding entry in the catalog is highlighted. Here you can determine the SID of the source.
Take the source with SID 16246 in the SourceList with SLID 423431.

## GalPhot: Isophotal analysis: GalPhot

It is instructive to first read the [Galphot HOW-TO](http://doc.astro-wise.org/man_howto_galphot.html), in particular to get an idea of the names of classes and methods defined for Galphot.

Isophotes can be fit to sources using the Galphot package. The main classes used to store the information of the fit are `GalPhotModel` and `GalPhotEllipse`. Lets follow an example here.

Use the GalPhotTask task to do the isophotal fits.

In [ ]:
task = GalPhotTask(slid=423431, sids=[16246], commit=True)
task.execute()

or

```
dpu.run('GalPhot', slid=423431, sids=[16246], C=1)
```

Inspect the model. We must start by finding the model we made in the previous step in the database. This can be done by selecting the most recent GalPhotModel created by yourself.

In [ ]:
m = (GalPhotModel.SLID == 423431).user_only().max('GPID')

The methods ``get_model()``, ``get_residual()``, ``get_science()`` can be used on a GalPhotModel to visually inspect its quality.

In [ ]:
s = m.get_science()
s.inspect()
r = m.get_residual()
r.inspect()

The fitted ellipses are stored in the model, and they can also be obtained:

In [ ]:
m.ellipses[0].r

For a description of the ellipse parameters see the help page of one of the ellipses:

help(m.ellipses[0])

```
Help on GalPhotEllipse in module astro.main.GalPhotModel object:

class GalPhotEllipse(common.database.DBMain.DBObject, astro.main.SourceLink.SourceLink, astro.main.ProcessTarget.ProcessTarget)
 |  This describes one ellipse as calculated by GalPhot. A GalPhotModel
 |  consists of a number of GalPhotEllipses
 |  
 |  Method resolution order:
 |      GalPhotEllipse
 |      common.database.DBMain.DBObject
 |      astro.main.SourceLink.SourceLink
 |      astro.main.ProcessTarget.ProcessTarget
 |      common.database.DBMeta.DBMixin
 |      common.main.ProcessTarget.ProcessTarget
 |      astro.main.OnTheFly.OnTheFly
 |      common.main.OnTheFly.OnTheFly
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  get_ellipse_parameters(self)
 |  
 |  show_ellipse_parameters(self)
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  GPID
 |      Galphot ID [None]
 |  
 |  GPLID
 |      Galphot List identifier [None]
 |  
 |  SID
 |      Source identifier [None]
 |  
 |  SLID
 |      SourceList identifier [None]
 |  
 |  c1
 |      The cos(n*theta) term of the residuals along the ellipse [None]
 |  
 |  c2
 |      The cos(n*theta) term of the residuals along the ellipse [None]
 |  
 |  c3
 |      The cos(n*theta) term of the residuals along the ellipse [None]
 etc.
 ```

You can obtain/visualize the ellipse parameters:

In [ ]:
ellipses = m.get_model_parameters()
rad = [e['r'] for e in ellipses]
pos = [e['pos'] for e in ellipses]
pylab.scatter(rad, pos)

For more information see the [Galphot HOW-TO](http://doc.astro-wise.org/man_howto_galphot.html).

## GalFit: 2D Parametric fits to a galaxy surface brightness distribution

The main classes used to store Galfit models are GalFitModel and a number of classes named e.g. GalFitSeric, each of which is a function that can be fit to the data. See the first section of the Galfit HOW-TO for an overview of the important classes defined for using Galfit in Astro-WISE.

Here too, **we first need to identify a source on which we want to run Galfit**. We can take the same source as in the previous example, the source from the SourceList with SLID 423431 and SID 16246.

**Create a Sersic model for the galaxy where the index of the Sersic model is fixed at 3.** The model components are specified as a list of dictionaries. Each dictionary describes one component. (Physical) component parameters come in 3 variants e.g.: **ix**, **x**, **dx**, respectively the initial, final and error values. Additionally the parameter is set to be fixed or free with the **free_x** parameter.

In [ ]:
task = GalFitTask(slid=423431, sids=[16246], models=[{'name': 'sersic', 'iN': 3, 'free_N': 0}],
                  commit=True)
task.execute()

or

```
dpu.run('GalFit', i='WFI', slid=423431, sids=[16246], m=[{'name': 'sersic', 'iN': 3, 'free_N': 0}], C=1)
```

Again we need to find the result in the database:

In [ ]:
m = (GalFitModel.SLID == 423431).user_only().max('GFID')

Now we can inspect the model: retrieve the residual image of the science and the model.

In [ ]:
sci = m.get_science()
res = m.get_residual()
mod = m.get_model()
sci.inspect()
res.inspect()
mod.inspect()

etc.
Have a look at the parameters of the model:

In [ ]:
m.show_model_parameters()

or

In [ ]:
m.info()
m.components[0].info()

For more information see the [Galfit HOW-TO](http://doc.astro-wise.org/man_howto_galfit.html).